In [90]:
from pyspark.sql import SparkSession
from pyspark.context import SparkContext
from pyspark import SQLContext
from pyspark.sql import functions as F
from pyspark.sql.functions import udf, col
from pyspark.sql.functions import when
from pyspark.sql.types import IntegerType,StringType,StructType,DoubleType,TimestampType
from pyspark.sql.functions import col
from dateutil.parser import parser, parse
import pyspark
import logging
import traceback
import sys
import os
import json
import re
import datetime

In [2]:
spark = SparkSession \
        .builder \
        .appName("Novo Data processing") \
        .config("spark.some.config.option", "NovoData") \
        .getOrCreate()        
    

Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/06/28 12:49:51 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
conf = pyspark.SparkConf()
spark = SparkSession.builder.config(conf=conf).getOrCreate()
sqlcontext = SQLContext(spark)

/opt/conda/lib/python3.8/site-packages/pyspark/sql/context.py:77: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


In [4]:
api_homeownership_DF = spark.read.format("csv").option("header",True).load('input/api_homeownership.csv')
api_oldcustomer_DF = spark.read.format("csv").option("header",True).load('input/api_oldcustomer.csv')
api_newcustomer_DF = spark.read.format("csv").option("header",True).load('input/api_newcustomer.csv')
api_purpose_DF = spark.read.format("csv").option("header",True).load('input/api_purpose.csv')
api_subgrade_DF = spark.read.format("csv").option("header",True).load('input/api_subgrade.csv')
api_verificationstatus_DF = spark.read.format("csv").option("header",True).load('input/api_verificationstatus.csv')
api_state_DF = spark.read.format("csv").option("header",True).load('input/api_state.csv')

In [5]:
api_homeownership_DF.printSchema()
api_oldcustomer_DF.printSchema()
api_newcustomer_DF.printSchema() 
api_purpose_DF.printSchema() 
api_subgrade_DF.printSchema() 
api_verificationstatus_DF.printSchema() 
api_state_DF.printSchema()

root
 |-- id: string (nullable = true)
 |-- name: string (nullable = true)

root
 |-- id: string (nullable = true)
 |-- loan_status_2: string (nullable = true)
 |-- loan_status: string (nullable = true)
 |-- loan_amnt: string (nullable = true)
 |-- term: string (nullable = true)
 |-- int_rate: string (nullable = true)
 |-- installment: string (nullable = true)
 |-- sub_grade: string (nullable = true)
 |-- emp_length: string (nullable = true)
 |-- home_ownership: string (nullable = true)
 |-- annual_inc: string (nullable = true)
 |-- verification_status: string (nullable = true)
 |-- issue_d: string (nullable = true)
 |-- purpose: string (nullable = true)
 |-- addr_state: string (nullable = true)
 |-- dti: string (nullable = true)
 |-- fico_range_low: string (nullable = true)
 |-- fico_range_high: string (nullable = true)
 |-- open_acc: string (nullable = true)
 |-- pub_rec: string (nullable = true)
 |-- revol_bal: string (nullable = true)
 |-- revol_util: string (nullable = true)
 |-- 

In [43]:
@udf
def convert_str_to_number(column):
    total_stars = 0
    num_map = {'K':1000, 'M':1000000, 'B':1000000000}
    if column.isdigit():
        total_stars = int(column)
    else:
        if len(column) > 1:
            total_stars = float(column[:-1]) * num_map.get(column[-1].upper(), 1)
    return int(total_stars)

@udf
def convert_str_to_months(x):
    str_months = x.split(".")
    months = (int(str_months[0])* 12)
    print(months)
    return months
    
@udf    
def convert_decimal_to_int(str):
    if str == "NULL" or str == " " or str is None:
        str = 0
        number = float(str)
        intvalue = int(number)

    else:
        new_number = float(str)
        intvalue = int(new_number)
        

    print(intvalue)
    return intvalue


@udf
def parse_date(dt_str):   

    default_date = datetime.datetime.strptime('01/01/01', '%m/%d/%y')

    dt = parse(dt_str, default = default_date)
    
    return dt

In [63]:
newcustomer_df = api_newcustomer_DF.withColumn("loan_amnt", convert_str_to_number(col('loan_amnt'))) \
    .withColumn("term", convert_str_to_months(col('term'))) \
    .withColumn("fico_range_low", convert_decimal_to_int(col('fico_range_low'))) \
    .withColumn("fico_range_high", convert_decimal_to_int(col('fico_range_high'))) \
    .withColumn("open_acc", convert_decimal_to_int(col('open_acc'))) \
    .withColumn("pub_rec", convert_decimal_to_int(col('pub_rec'))) \
    .withColumn("revol_bal", convert_decimal_to_int(col('revol_bal'))) \
    .withColumn("mort_acc", convert_decimal_to_int(col('mort_acc'))) \
    .withColumn("pub_rec_bankruptcies", convert_decimal_to_int(col('pub_rec_bankruptcies'))) \
    .withColumn("age", convert_decimal_to_int(col('age'))) \
    .withColumn("payment_status", convert_decimal_to_int(col('payment_status')))

In [64]:
newcustomer_df.createOrReplaceTempView("newcustomer")
api_homeownership_DF.createOrReplaceTempView("homeownership")
api_purpose_DF.createOrReplaceTempView("purpose")
api_subgrade_DF.createOrReplaceTempView("subgrade")
api_verificationstatus_DF.createOrReplaceTempView("verificationstatus")
api_state_DF.createOrReplaceTempView("state")

In [ ]:
new_df.coalesce(1).write.option("header",True) \
.csv("output/2")

In [74]:
new_new_customer = spark.sql("""select new.id,IF(new.loan_status = 0, "Paid", "Written off") as loan_status_2,
              new.loan_status,new.loan_amnt,new.term,new.int_rate,new.installment,
              sub.name as sub_grade,new.employment_length as emp_length,home.name as home_ownership,
              new.annual_inc,vefify.name as verification_status, new.issued as issue_d,
              pur.name as purpose,st.name as addr_state, new.dti, new.fico_range_low, 
              new.fico_range_high, new.open_acc, new.pub_rec, new.revol_bal,
              new.revol_util,new.mort_acc,new.pub_rec_bankruptcies,new.age,
              new.payment_status as pay_status 
              from newcustomer new  
              left join subgrade sub on new.sub_grade_id = sub.id  
              left join homeownership home on new.home_ownership_id = home.id 
              left join verificationstatus vefify on new.verification_status_id = vefify.id 
              left join purpose pur on new.purpose_id = pur.id 
              left outer join state st on new.addr_state_id = st.id """)

In [79]:
api_oldcustomer_DF.createOrReplaceTempView("oldcustomer")

In [80]:
final_df = new_new_customer.union(api_oldcustomer_DF)

In [113]:
final_df = final_df.withColumn("is_mortgage", when(final_df.home_ownership == "MORTGAGE","YES").otherwise("NO"))  \
                   .withColumn("is_rent", when(final_df.home_ownership == "RENT","YES").otherwise("NO")) \
                   .withColumn("is_own", when(final_df.home_ownership == "OWN","YES").otherwise("NO"))  \
                   .withColumn("is_any", when(final_df.home_ownership == "ANY","YES").otherwise("NO"))  \
                   .withColumn("is_other", when(final_df.home_ownership == "OTHER","YES").otherwise("NO")) \
                   .withColumn("is_verified", when(final_df.verification_status == "Verified","YES").otherwise("NO"))  \
                   .withColumn("is_not_verified", when(final_df.home_ownership == "Not Verified","YES").otherwise("NO"))  \
                   .withColumn("is_source_verified", when(final_df.home_ownership == "Source Verified","YES").otherwise("NO")) \
                   .drop("ID","loan_status_2")




                               


In [114]:
final_df.coalesce(1).write.option("header",True) \
.csv("output/final7")

36tage 87:>                                                         (0 + 1) / 1]
770
774
7
0
6112
2
0
27
0
36
695
699
10
1
12641
1
1
32
-1
36
720
724
8
0
81
3
0
30
0
36
700
704
9
0
29025
8
0
27
0
36
710
714
3
0
3824
0
0
28
0
36
665
0
8
0
8031
0
0
28
1
36
660
664
11
0
10543
0
0
28
1
36
685
689
9
0
4987
1
0
27
-2
36
660
664
14
0
6999
3
0
28
0
60
705
709
9
0
23126
0
0
26
-1
36
675
679
13
0
16142
4
0
24
4
60
690
694
12
1
6623
2
1
31
0
36
770
774
19
0
8365
1
0
29
0
36
725
729
8
0
35277
2
0
27
2
36
740
744
8
0
14495
0
0
23
0
60
705
709
14
0
8584
3
0
27
3
36
735
739
5
0
5180
0
0
28
-1
36
665
0
6
0
7182
0
0
28
1
36
710
714
20
0
13757
1
0
28
0
36
685
689
10
0
15705
2
0
28
-1
60
740
744
9
0
38732
3
0
28
5
36
670
674
6
0
11181
1
0
25
0
60
660
664
17
0
24189
7
0
30
0
60
680
0
13
0
9941
0
0
25
0
60
675
679
9
0
4385
0
0
30
0
36
685
689
14
0
46519
0
0
28
0
36
710
714
5
0
10194
0
0
28
0
36
735
739
23
0
3998
8
0
28
0
60
665
0
16
0
10651
1
0
28
0
36
675
679
7
0
8235
4
0
28
1
36
665
0
6
0
1609
1
0
30
1
6

In [ ]:
new_df = api_newcustomer_DF.withColumn("loan_amnt", convert_str_to_number(col('loan_amnt'))).withColumn("term", convert_str_to_months(col('term')))

In [ ]:
@udf
def parse_date(dt_str):   

    default_date = datetime.datetime.strptime('01/01/01', '%m/%d/%y')

    dt = parse(dt_str, default = default_date)
    
    return dt


In [ ]:
print_df=new_df.withColumn("issued", parse_date(col('issued')))


In [ ]:
parse_date_udf = udf(parse_date)
new_df.select(parse_date_udf(new_df.issued))

In [24]:
str = "2.0"
num = float(str)
print(int(num))

2


In [ ]:
new_df.withColumn("issued", parse_date(col('issued'))).show(1)
df=new_df.withColumn("issued", parse_date(col('issued')))
parse_date_udf = udf(parse_date)
new_df.select(parse_date_udf(new_df.issued)).take(2)

In [ ]:
new_df.write.csv("output/results")

In [ ]:
default_date = datetime.datetime.strptime('01/01/01', '%m/%d/%y')

complete_date = 'May 4, 2017'
incomplete_date = '2013-01'

print(parse(complete_date, default=jan_01_2001) == parse(complete_date, default=feb_02_2002))
# True

print(parse(incomplete_date, default=jan_01_2001) == parse(incomplete_date, default=feb_02_2002))
# False


print(parse(incomplete_date, default=default_date))

In [ ]:
df.rdd.map(lambda row:date_convert(row.C3)).collect()
date_convert_udf = udf(date_convert)
df.select(date_convert_udf(df.C3).alias("datetime")).take(2)

In [115]:
from pyspark.sql import SparkSession
from pyspark.context import SparkContext
from pyspark import SQLContext
from pyspark.sql import functions as F
from pyspark.sql.functions import udf, col
from pyspark.sql.functions import when
from pyspark.sql.types import IntegerType,StringType,StructType,DoubleType,TimestampType
from pyspark.sql.functions import col
from dateutil.parser import parser, parse
import pyspark
import logging
import traceback
import sys
import os
import json
import re
import datetime

@udf
def convert_str_to_number(column):
    total_stars = 0
    num_map = {'K':1000, 'M':1000000, 'B':1000000000}
    if column.isdigit():
        total_stars = int(column)
    else:
        if len(column) > 1:
            total_stars = float(column[:-1]) * num_map.get(column[-1].upper(), 1)
    return int(total_stars)

@udf
def convert_str_to_months(x):
    str_months = x.split(".")
    months = (int(str_months[0])* 12)
    print(months)
    return months
    
@udf    
def convert_decimal_to_int(x):
    int_value = int(round(x))
    print(int_value)
    return int_value

@udf
def parse_date(dt_str):   

    default_date = datetime.datetime.strptime('01/01/01', '%m/%d/%y')

    dt = parse(dt_str, default = default_date)

    d = dt.strftime("%Y-%m-%d %H:%M:%S")
    
    return d


In [116]:

if __name__ == "__main__":

    # This is a pyspark docker container(jupyter), Spark context is already available if not please add it here
    #Logging configuration
    logging.basicConfig(filename='logs/debug.log',level=logging.DEBUG,format='%(asctime)s %(levelname)s:%(message)s', datefmt='%m/%d/%Y %H:%M:%S')
    logging.disable(logging.DEBUG)

    #sparksession  
    try:

        spark = SparkSession \
            .builder \
            .appName("ADC Data processing") \
            .config("spark.some.config.option", "ADC") \
            .getOrCreate()        
        
        logging.info('SparkSession created')
                    
    except:
        
        logging.error(str(traceback.format_exc()))
        sys.exit()

    logging.info('DataFrames created for each table/CSV file')
    api_homeownership_DF = spark.read.format("csv").option("header",True).load('input/api_homeownership.csv')
    api_oldcustomer_DF = spark.read.format("csv").option("header",True).load('input/api_oldcustomer.csv')
    api_newcustomer_DF = spark.read.format("csv").option("header",True).load('input/api_newcustomer.csv')
    api_purpose_DF = spark.read.format("csv").option("header",True).load('input/api_purpose.csv')
    api_subgrade_DF = spark.read.format("csv").option("header",True).load('input/api_subgrade.csv')
    api_verificationstatus_DF = spark.read.format("csv").option("header",True).load('input/api_verificationstatus.csv')
    api_state_DF = spark.read.format("csv").option("header",True).load('input/api_state.csv')

    logging.info('DataFrames Schemas for each table')
    api_homeownership_DF.printSchema()
    api_oldcustomer_DF.printSchema()
    api_newcustomer_DF.printSchema()
    api_purpose_DF.printSchema()
    api_subgrade_DF.printSchema()
    api_verificationstatus_DF.printSchema()
    api_state_DF.printSchema()
    

    logging.info('newcustomer_df after transformations')
    newcustomer_df = api_newcustomer_DF.withColumn("loan_amnt", convert_str_to_number(col('loan_amnt'))) \
    .withColumn("issued", parse_date(col('issued'))) \
    .withColumn("term", convert_str_to_months(col('term'))) \
    .withColumn("fico_range_low", convert_decimal_to_int(col('fico_range_low'))) \
    .withColumn("fico_range_high", convert_decimal_to_int(col('fico_range_high'))) \
    .withColumn("open_acc", convert_decimal_to_int(col('open_acc'))) \
    .withColumn("pub_rec", convert_decimal_to_int(col('pub_rec'))) \
    .withColumn("revol_bal", convert_decimal_to_int(col('revol_bal'))) \
    .withColumn("mort_acc", convert_decimal_to_int(col('mort_acc'))) \
    .withColumn("pub_rec_bankruptcies", convert_decimal_to_int(col('pub_rec_bankruptcies'))) \
    .withColumn("age", convert_decimal_to_int(col('age'))) \
    .withColumn("payment_status", convert_decimal_to_int(col('payment_status')))


    logging.info('Creating temp tables on spark dataframe to perform SQL')
    newcustomer_df.createOrReplaceTempView("newcustomer")
    api_homeownership_DF.createOrReplaceTempView("homeownership")
    api_purpose_DF.createOrReplaceTempView("purpose")
    api_subgrade_DF.createOrReplaceTempView("subgrade")
    api_verificationstatus_DF.createOrReplaceTempView("verificationstatus")
    api_state_DF.createOrReplaceTempView("state")
    api_oldcustomer_DF.createOrReplaceTempView("oldcustomer")
        

    logging.info('SparkSQl query to fetch the data from different table by joining ')   
    new_new_customer = spark.sql("""select new.id,IF(new.loan_status = 0, "Paid", "Written off") as loan_status_2,
                new.loan_status,new.loan_amnt,new.term,new.int_rate,new.installment,
                sub.name as sub_grade,new.employment_length as emp_length,home.name as home_ownership,
                new.annual_inc,vefify.name as verification_status, new.issued as issue_d,
                pur.name as purpose,st.name as addr_state, new.dti, new.fico_range_low, 
                new.fico_range_high, new.open_acc, new.pub_rec, new.revol_bal,
                new.revol_util,new.mort_acc,new.pub_rec_bankruptcies,new.age,
                new.payment_status as pay_status 
                from newcustomer new  
                left join subgrade sub on new.sub_grade_id = sub.id  
                left join homeownership home on new.home_ownership_id = home.id 
                left join verificationstatus vefify on new.verification_status_id = vefify.id 
                left join purpose pur on new.purpose_id = pur.id 
                left join state st on new.addr_state_id = st.id """)


    logging.info('Union query to merging the 2 data sets newcustomer and oldcustomer tables')  
    final_df = new_new_customer.union(api_oldcustomer_DF)


    logging.info('Adding the new derived columns to dataset')  
    final_df = final_df.withColumn("is_mortgage", when(final_df.home_ownership == "MORTGAGE","YES").otherwise("NO"))  \
                   .withColumn("is_rent", when(final_df.home_ownership == "RENT","YES").otherwise("NO")) \
                   .withColumn("is_own", when(final_df.home_ownership == "OWN","YES").otherwise("NO"))  \
                   .withColumn("is_any", when(final_df.home_ownership == "ANY","YES").otherwise("NO"))  \
                   .withColumn("is_other", when(final_df.home_ownership == "OTHER","YES").otherwise("NO")) \
                   .withColumn("is_verified", when(final_df.verification_status == "Verified","YES").otherwise("NO"))  \
                   .withColumn("is_not_verified", when(final_df.home_ownership == "Not Verified","YES").otherwise("NO"))  \
                   .withColumn("is_source_verified", when(final_df.home_ownership == "Source Verified","YES").otherwise("NO")) \
                   .drop("ID","loan_status_2")
    

    logging.info('Writing the dataset to CSV file')  
    final_df.coalesce(1).write.option("header",True) \
        .csv("output/final7")








root
 |-- id: string (nullable = true)
 |-- name: string (nullable = true)

root
 |-- id: string (nullable = true)
 |-- loan_status_2: string (nullable = true)
 |-- loan_status: string (nullable = true)
 |-- loan_amnt: string (nullable = true)
 |-- term: string (nullable = true)
 |-- int_rate: string (nullable = true)
 |-- installment: string (nullable = true)
 |-- sub_grade: string (nullable = true)
 |-- emp_length: string (nullable = true)
 |-- home_ownership: string (nullable = true)
 |-- annual_inc: string (nullable = true)
 |-- verification_status: string (nullable = true)
 |-- issue_d: string (nullable = true)
 |-- purpose: string (nullable = true)
 |-- addr_state: string (nullable = true)
 |-- dti: string (nullable = true)
 |-- fico_range_low: string (nullable = true)
 |-- fico_range_high: string (nullable = true)
 |-- open_acc: string (nullable = true)
 |-- pub_rec: string (nullable = true)
 |-- revol_bal: string (nullable = true)
 |-- revol_util: string (nullable = true)
 |-- 

AnalysisException: path file:/opt/spark/output/final7 already exists.